In [1]:
%matplotlib qt

import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

In [2]:
def AddHill(Z,NX,NY,xx,yy,r,h):

    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; 
            dy = np.mod(y-yy+NY/2,NY)-NY/2;
            dr = np.sqrt(dx**2+dy**2);
            if (dr<r):
                Z[x,y] += h * (np.cos(dr/r*np.pi/2.0))**2;

    return Z

In [3]:

NX = 50*2
NY = 50*2 

d  = 5 
dx = d 
dy = d

LX=NX*dx
LY=NY*dy


xs=[0.01,0.3,0.450,0.60,0.80]
ys=[0.9,0.7,0.5,0.30,0.20]

Z = rand(NX,NY)*0.1
for i in range(5):
    xx = xs[i]*NX
    yy = ys[i]*NY
    r  = (0.1+1)*NX
    h  = (0.1+1)*577.7
    Z = AddHill(Z,NX,NY,xx,yy,r,h)

for i in range(5):
    xx = xs[i]*NX
    yy = ys[i]*NY
    r  = (0.1+1)*NX/2
    h  = (0.5+1)*577.7
    Z = AddHill(Z,NX,NY,xx,yy,r,h)

x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) 
ZMaxOrg = np.max(Z)


In [4]:

K = 1.0e-6

D = 0.005 


uplift = 0.0

In [5]:

dt = 466
print(' dt[years] = ',dt)
m=1

n=1 
theta_c = 10 

 dt[years] =  466


In [6]:

T = 1000.0 * dt
n_iter = int(np.round(T/dt))
print('Number of interation: ',n_iter)

Number of interation:  1000


In [7]:

ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=-1 
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           2762.961832395762
Maximum elevation           4421.2582364853
Beach level                 1104.6654283062244
Ocean volume                0.0
Percentage of ocean surface 0.0


In [8]:

def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure(it):
        global dt
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title('Elevation')

        im = ax2.pcolor(ZPlot,cmap=cm.coolwarm)
        cs = ax2.contour(ZPlot,6,colors='k')

        
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        cbar.add_lines(cs)
        ax2.title.set_text('Time elapsed: {} years'.format(it *dt))

        plt.draw()
        plt.pause(0.0001)

In [ ]:

fig = init_figure()
it=0
update_figure(it)

Znew = np.copy(Z)

from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)
with writer.saving(fig, "problem0.mp4", dpi=200):

    for it in range(1,n_iter+1):
        writer.grab_frame()

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) 
            iR = np.mod(i+1,NX) 

            for j in range(NY):
                jD = np.mod(j-1,NY)
                jU = np.mod(j+1,NY) 

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: 
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0:

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx 
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else:
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. 

        
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,10)==0): 
            print(it,end='')
            update_figure(it)
            print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')

    update_figure(it)
    print(' Simulation finished.')


.




























































































































.















































































































































.
















































































































































.


































































































































































.

















































































































...

50 Ocean level= 0.0  Ocean surface fraction= 0.01












































































































































































































































































































































.





































































































































































































































































































































.





































































































































































































































































































































.
















































































































































































































.